In [1]:
import numpy as np
import pandas as pd
import nltk
from nltk import word_tokenize
from nltk.corpus import stopwords
from gensim.models import word2vec

nltk.download('stopwords')
nltk.download('punkt')

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\95804\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\95804\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

In [2]:
df = pd.read_csv('data/train.csv')
df = df.iloc[:, -2:]
df

label  \
0      american (traditional)   
1              american (new)   
2                     mexican   
3                     mexican   
4                     chinese   
...                       ...   
13139                 mexican   
13140                 italian   
13141                 mexican   
13142                japanese   
13143                 chinese   

                                                  review  
0      So, we stopped here on our way to the Side Que...  
1      This is our go-to healthy spot! The food is al...  
2      Food court meal at Gerrard Square.  It's been ...  
3      Located on Rainbow/Charleston, this small fami...  
4      No frills Chinese takeout joint which serves u...  
...                                                  ...  
13139  Worst food ever...they should be ashamed to ca...  
13140  My experience with this restaurant is a little...  
13141  Giving them one star to just write my review. ...  
13142  It was a good deal with the voucher. However, ...  
13143  I don't write that many reviews but this place...  

[13144 rows x 2 columns]

# Preprocessing

### Tokenization

In [4]:
# Download NLTK resources
nltk.download('punkt')
nltk.download('stopwords')
stop_words = set(stopwords.words('english'))

# Initialize Porter Stemmer
stemmer = PorterStemmer()
stemmed_stop_words = {stemmer.stem(word.lower()) for word in stop_words}

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\95804\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\95804\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [6]:
from nltk.stem import PorterStemmer
import re

ps = PorterStemmer() 

punc = r'[^\w\s]'

stem_doc = []
for sentence in df['review'].values:
    tok = word_tokenize(sentence)
    words = [ps.stem(word) for word in tok]
    word_stopped = [word for word in words if (word not in stemmed_stop_words) and (not re.match(punc, word))]
    stem_doc.append(word_stopped)

stem_doc

[['stop',
  'way',
  'side',
  'quest',
  'street',
  'know',
  'expect',
  'came',
  '3',
  'taco',
  'night',
  'glad',
  'rush',
  'inn',
  'bar-ish',
  'place',
  'plenti',
  'back',
  'side',
  'seat',
  'booth',
  'place',
  'dark',
  'rich',
  'wood',
  'tone',
  'patron',
  'decent',
  'folks.\\n\\nth',
  'taco',
  'except',
  'select',
  'quit',
  'good',
  'sort',
  'stuff',
  'intend',
  'tri',
  'soon',
  'possibl',
  'think',
  'place',
  'would',
  'make',
  'nice',
  'casual',
  'dinner/lunch',
  'stop',
  'need',
  'get',
  'beverag',
  'barkeep',
  'wait',
  'staff',
  'keep',
  'em',
  'come',
  'quick',
  'tasti',
  'bite',
  "n't",
  'walk',
  'slow',
  'rush',
  'rush',
  'inn',
  'boyfriend',
  'heard',
  'littl',
  'place',
  'near',
  'rush',
  'inn',
  'offer',
  'board',
  'game',
  'poutin',
  'friday',
  'arriv',
  "n't",
  'food',
  'chef',
  "n't",
  'show',
  'ventur',
  'place',
  'block',
  'great',
  'vibe',
  'insid',
  'typic',
  'bar',
  'scene',
  

In [ ]:
labels = df['label'].values

# Modeling

### LSTM (deep learning)

In [11]:
import numpy as np
from sklearn.preprocessing import MultiLabelBinarizer
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Embedding, LSTM, Dense

labels = df['label'].values
# Tokenize the text data
tokenizer = Tokenizer()
tokenizer.fit_on_texts([' '.join(sentence) for sentence in stem_doc])
sequences = tokenizer.texts_to_sequences([' '.join(sentence) for sentence in stem_doc])

# Pad sequences to ensure uniform length
max_sequence_length = max([len(seq) for seq in sequences])
padded_sequences = pad_sequences(sequences, maxlen=max_sequence_length)
padded_sequences

array([[    0,     0,     0, ...,   447,  1052,    89],
       [    0,     0,     0, ...,   121,    28,   266],
       [    0,     0,     0, ...,   369,     4, 14188],
       ...,
       [    0,     0,     0, ...,    29,     1,   171],
       [    0,     0,     0, ...,    19,    87,     1],
       [    0,     0,     0, ...,    12,  6452,  1226]])

In [12]:
np.shape(padded_sequences)

(13144, 1594)

In [14]:
np.shape(binary_labels)

(13144, 10)

In [10]:
# Convert labels into binary vectors using MultiLabelBinarizer
mlb = MultiLabelBinarizer()
binary_labels = mlb.fit_transform([[label] for label in labels])

# Define the LSTM model architecture
embedding_dim = 100  # Dimension of the word embeddings
model = Sequential()
model.add(Embedding(input_dim=len(tokenizer.word_index) + 1, output_dim=embedding_dim))
model.add(LSTM(units=128, dropout=0.2, recurrent_dropout=0.2))
model.add(Dense(len(labels), activation='sigmoid'))

# Compile the model
model.compile(optimizer='adam', loss='binary_crossentropy', metrics=['accuracy'])

# Train the model
model.fit(padded_sequences, binary_labels, epochs=10, batch_size=32, validation_split=0.2)


Epoch 1/10


ValueError: Arguments `target` and `output` must have the same shape. Received: target.shape=(None, 10), output.shape=(None, 13144)